In [49]:
# Импортируем необходимые библиотеки

import time

import pandas as pd
import numpy as np

from sklearn.model_selection import train_test_split
#from sklearn.model_selection import KFold
from sklearn.metrics import *
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV

#from sklearn.feature_extraction.text import CountVectorizer
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from sklearn.tree import ExtraTreeRegressor
from tqdm import tqdm
from catboost import CatBoostRegressor
from sklearn.linear_model import LinearRegression
import lightgbm as lgb

In [2]:
import warnings

warnings.filterwarnings('ignore')

In [3]:
# всегда фиксируйте RANDOM_SEED, чтобы ваши эксперименты были воспроизводимы!
RANDOM_SEED = 42

In [4]:
# зафиксируем версию пакетов, чтобы эксперименты были воспроизводимы:
!pip freeze > requirements.txt

In [5]:
# загрузка обработанного датасета
bgg_df = pd.read_csv('data/bgg_data_for_ml.csv')

In [6]:
bgg_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 168507 entries, 0 to 168506
Data columns (total 63 columns):
 #   Column                Non-Null Count   Dtype  
---  ------                --------------   -----  
 0   rating                168507 non-null  float64
 1   bayes_rating          168507 non-null  float64
 2   usersrated            168507 non-null  int64  
 3   bggrank               168507 non-null  int64  
 4   stddev                168507 non-null  float64
 5   owned                 168507 non-null  int64  
 6   trading               168507 non-null  int64  
 7   wanting               168507 non-null  int64  
 8   wishing               168507 non-null  int64  
 9   numweights            168507 non-null  int64  
 10  averageweight         168507 non-null  float64
 11  yearpublished         168507 non-null  int64  
 12  minplayers            168507 non-null  int64  
 13  maxplayers            168507 non-null  int64  
 14  minplaytime           168507 non-null  float64
 15  

## Подбор модели машинного обучения

In [7]:
y = bgg_df['rating']

x = bgg_df.drop('rating', axis=1)

In [8]:
# Создадим тренировочную и валидационную выборки
x_train, x_val, y_train, y_val = train_test_split(x, y,
                                                  test_size=0.2,
                                                  shuffle=True,
                                                  random_state=RANDOM_SEED)

In [9]:
# Функции расчета ошибки

def MAE(y_true, y_pred):
    
    abs_error = np.abs(y_pred - y_true)
    sum_abs_error = np.sum(abs_error)
    
    return sum_abs_error / y_true.size

### 1. Обучим простую модель - Линейную регрессию

In [10]:
%%time
lr_model = LinearRegression()
lr_model.fit(x_train, y_train)

lr_predict = lr_model.predict(x_val)
# оцениваем точность
print(f"Точность модели по метрике MAE: {(MAE(y_val, lr_predict)):0.2f}")

Точность модели по метрике MAE: 1.19
CPU times: total: 3.81 s
Wall time: 844 ms


In [11]:
%%time
estimate = -1 * cross_val_score(lr_model,
                           x_train,
                           y_train,
                           cv=10,
                           scoring='neg_mean_absolute_error')

print(f"Точность модели по метрике MAE: {estimate.mean():0.2f}")

Точность модели по метрике MAE: 1.20
CPU times: total: 40.4 s
Wall time: 7.51 s


### 2. RandomForestRegressor

In [15]:
%%time
param_rfr_grid = [
{
    'n_estimators': [100],
    'random_state': [RANDOM_SEED],
    'min_samples_split': [5],
    'min_samples_leaf': [2],
    'max_features': ['auto', 'sqrt', 'log2']
},
{
    'bootstrap': [False],
    'n_estimators': [100],
    'random_state': [RANDOM_SEED],
    'min_samples_split': [5],
    'min_samples_leaf': [2],
    'max_features': ['auto', 'sqrt', 'log2']
},
]

forest_reg = RandomForestRegressor()
grid_search = GridSearchCV(forest_reg,
                           param_rfr_grid,
                           cv=5,
                           verbose=3,
                           scoring='neg_mean_absolute_error')
 
grid_search.fit(x_train.values,np.ravel(y_train.values))

Fitting 5 folds for each of 6 candidates, totalling 30 fits
[CV 1/5] END max_features=auto, min_samples_leaf=2, min_samples_split=5, n_estimators=100, random_state=42;, score=-0.701 total time= 2.8min
[CV 2/5] END max_features=auto, min_samples_leaf=2, min_samples_split=5, n_estimators=100, random_state=42;, score=-0.704 total time= 2.8min
[CV 3/5] END max_features=auto, min_samples_leaf=2, min_samples_split=5, n_estimators=100, random_state=42;, score=-0.695 total time= 2.8min
[CV 4/5] END max_features=auto, min_samples_leaf=2, min_samples_split=5, n_estimators=100, random_state=42;, score=-0.688 total time= 2.8min
[CV 5/5] END max_features=auto, min_samples_leaf=2, min_samples_split=5, n_estimators=100, random_state=42;, score=-0.705 total time= 2.8min
[CV 1/5] END max_features=sqrt, min_samples_leaf=2, min_samples_split=5, n_estimators=100, random_state=42;, score=-0.717 total time=  24.0s
[CV 2/5] END max_features=sqrt, min_samples_leaf=2, min_samples_split=5, n_estimators=100, ran

GridSearchCV(cv=5, estimator=RandomForestRegressor(),
             param_grid=[{'max_features': ['auto', 'sqrt', 'log2'],
                          'min_samples_leaf': [2], 'min_samples_split': [5],
                          'n_estimators': [100], 'random_state': [42]},
                         {'bootstrap': [False],
                          'max_features': ['auto', 'sqrt', 'log2'],
                          'min_samples_leaf': [2], 'min_samples_split': [5],
                          'n_estimators': [100], 'random_state': [42]}],
             scoring='neg_mean_absolute_error', verbose=3)

In [16]:
print(grid_search.best_params_)
print(f"Точность модели по метрике MAE: {grid_search.best_score_:0.2f}")

{'max_features': 'auto', 'min_samples_leaf': 2, 'min_samples_split': 5, 'n_estimators': 100, 'random_state': 42}
Точность модели по метрике MAE: -0.70


In [17]:
%%time
rfr_model = RandomForestRegressor(n_estimators=500,
                                  max_features='auto',
                                  bootstrap=True,
                                  random_state = RANDOM_SEED,
                                  n_jobs = -1,
                                  verbose = 3,
                                  min_samples_split = 5,
                                  min_samples_leaf = 2)

rfr_model.fit(x_train, y_train)

[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 8 concurrent workers.


building tree 1 of 500building tree 2 of 500

building tree 3 of 500
building tree 4 of 500building tree 5 of 500
building tree 6 of 500building tree 7 of 500


building tree 8 of 500
building tree 9 of 500
building tree 10 of 500
building tree 11 of 500
building tree 12 of 500
building tree 13 of 500
building tree 14 of 500
building tree 15 of 500
building tree 16 of 500
building tree 17 of 500
building tree 18 of 500
building tree 19 of 500
building tree 20 of 500
building tree 21 of 500
building tree 22 of 500
building tree 23 of 500
building tree 24 of 500


[Parallel(n_jobs=-1)]: Done  16 tasks      | elapsed:    7.9s


building tree 25 of 500
building tree 26 of 500
building tree 27 of 500
building tree 28 of 500
building tree 29 of 500
building tree 30 of 500
building tree 31 of 500
building tree 32 of 500
building tree 33 of 500
building tree 34 of 500
building tree 35 of 500
building tree 36 of 500
building tree 37 of 500
building tree 38 of 500
building tree 39 of 500
building tree 40 of 500
building tree 41 of 500
building tree 42 of 500
building tree 43 of 500
building tree 44 of 500
building tree 45 of 500
building tree 46 of 500
building tree 47 of 500
building tree 48 of 500
building tree 49 of 500
building tree 50 of 500
building tree 51 of 500
building tree 52 of 500
building tree 53 of 500
building tree 54 of 500
building tree 55 of 500
building tree 56 of 500
building tree 57 of 500
building tree 58 of 500
building tree 59 of 500
building tree 60 of 500
building tree 61 of 500
building tree 62 of 500
building tree 63 of 500
building tree 64 of 500
building tree 65 of 500
building tree 66

[Parallel(n_jobs=-1)]: Done 112 tasks      | elapsed:   57.0s


building tree 121 of 500
building tree 122 of 500
building tree 123 of 500
building tree 124 of 500
building tree 125 of 500
building tree 126 of 500
building tree 127 of 500
building tree 128 of 500
building tree 129 of 500
building tree 130 of 500
building tree 131 of 500
building tree 132 of 500
building tree 133 of 500
building tree 134 of 500
building tree 135 of 500
building tree 136 of 500
building tree 137 of 500
building tree 138 of 500
building tree 139 of 500
building tree 140 of 500
building tree 141 of 500
building tree 142 of 500
building tree 143 of 500
building tree 144 of 500
building tree 145 of 500
building tree 146 of 500
building tree 147 of 500
building tree 148 of 500
building tree 149 of 500
building tree 150 of 500
building tree 151 of 500
building tree 152 of 500
building tree 153 of 500
building tree 154 of 500
building tree 155 of 500
building tree 156 of 500
building tree 157 of 500
building tree 158 of 500
building tree 159 of 500
building tree 160 of 500


[Parallel(n_jobs=-1)]: Done 272 tasks      | elapsed:  2.3min


building tree 281 of 500
building tree 282 of 500
building tree 283 of 500
building tree 284 of 500
building tree 285 of 500
building tree 286 of 500
building tree 287 of 500
building tree 288 of 500
building tree 289 of 500
building tree 290 of 500
building tree 291 of 500
building tree 292 of 500
building tree 293 of 500
building tree 294 of 500
building tree 295 of 500
building tree 296 of 500
building tree 297 of 500
building tree 298 of 500
building tree 299 of 500
building tree 300 of 500
building tree 301 of 500
building tree 302 of 500
building tree 303 of 500
building tree 304 of 500
building tree 305 of 500
building tree 306 of 500
building tree 307 of 500
building tree 308 of 500
building tree 309 of 500
building tree 310 of 500
building tree 311 of 500
building tree 312 of 500
building tree 313 of 500
building tree 314 of 500
building tree 315 of 500
building tree 316 of 500
building tree 317 of 500
building tree 318 of 500
building tree 319 of 500
building tree 320 of 500


[Parallel(n_jobs=-1)]: Done 500 out of 500 | elapsed:  4.1min finished


RandomForestRegressor(min_samples_leaf=2, min_samples_split=5, n_estimators=500,
                      n_jobs=-1, random_state=42, verbose=3)

In [18]:
rfr_predict = rfr_model.predict(x_val)

# оцениваем точность
print(f"Точность модели по метрике MAE: {(MAE(y_val, rfr_predict)):0.2f}")

[Parallel(n_jobs=8)]: Using backend ThreadingBackend with 8 concurrent workers.
[Parallel(n_jobs=8)]: Done  16 tasks      | elapsed:    0.0s
[Parallel(n_jobs=8)]: Done 112 tasks      | elapsed:    0.3s
[Parallel(n_jobs=8)]: Done 272 tasks      | elapsed:    0.8s


Точность модели по метрике MAE: 0.69


[Parallel(n_jobs=8)]: Done 500 out of 500 | elapsed:    1.5s finished


In [19]:
%%time
estimate_rfr = -1 * cross_val_score(rfr_model,
                           x_train,
                           y_train,
                           cv=5,
                           scoring='neg_mean_absolute_error')

print(f"Точность модели по метрике MAE: {estimate_rfr.mean():0.2f}")

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  16 tasks      | elapsed:   12.1s
[Parallel(n_jobs=-1)]: Done 112 tasks      | elapsed:   49.9s
[Parallel(n_jobs=-1)]: Done 272 tasks      | elapsed:  1.9min
[Parallel(n_jobs=-1)]: Done 500 out of 500 | elapsed:  3.4min finished
[Parallel(n_jobs=8)]: Using backend ThreadingBackend with 8 concurrent workers.
[Parallel(n_jobs=8)]: Done  16 tasks      | elapsed:    0.0s
[Parallel(n_jobs=8)]: Done 112 tasks      | elapsed:    0.2s
[Parallel(n_jobs=8)]: Done 272 tasks      | elapsed:    0.6s
[Parallel(n_jobs=8)]: Done 500 out of 500 | elapsed:    1.0s finished
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  16 tasks      | elapsed:    6.6s
[Parallel(n_jobs=-1)]: Done 112 tasks      | elapsed:   45.2s
[Parallel(n_jobs=-1)]: Done 272 tasks      | elapsed:  1.8min
[Parallel(n_jobs=-1)]: Done 500 out of 500 | elapsed:  3.3min finished
[

Точность модели по метрике MAE: 0.70
CPU times: total: 1min 15s
Wall time: 16min 40s


[Parallel(n_jobs=8)]: Done 500 out of 500 | elapsed:    1.1s finished


### 3. CatBoostRegressor

In [36]:
param_cbr_grid = {
    'iterations': range(1000, 4000, 1000),
    'learning_rate': [0.01, 0.05, 0.08, 0.1, 0.2],
    'l2_leaf_reg': range(1, 7, 1),
    'eval_metric': ['MAE'],
    'bootstrap_type': ['Bayesian', 'Bernoulli', 'MVS'],
    'random_seed': [RANDOM_SEED]
}


In [40]:
%%time
catboost_reg = CatBoostRegressor()

random_search = RandomizedSearchCV(catboost_reg,
                                   param_cbr_grid,
                                   cv=5,
                                   verbose = 3,
                                   scoring='neg_mean_absolute_error')
 
random_search.fit(x_train, y_train)

Fitting 5 folds for each of 10 candidates, totalling 50 fits
0:	learn: 2.1563861	total: 26.8ms	remaining: 1m 20s
1:	learn: 2.0841421	total: 49.4ms	remaining: 1m 14s
2:	learn: 2.0146749	total: 69.7ms	remaining: 1m 9s
3:	learn: 1.9514921	total: 90.3ms	remaining: 1m 7s
4:	learn: 1.8894136	total: 112ms	remaining: 1m 7s
5:	learn: 1.8300192	total: 134ms	remaining: 1m 7s
6:	learn: 1.7743132	total: 156ms	remaining: 1m 6s
7:	learn: 1.7220490	total: 176ms	remaining: 1m 5s
8:	learn: 1.6727155	total: 196ms	remaining: 1m 5s
9:	learn: 1.6255750	total: 220ms	remaining: 1m 5s
10:	learn: 1.5818535	total: 249ms	remaining: 1m 7s
11:	learn: 1.5399467	total: 269ms	remaining: 1m 6s
12:	learn: 1.5007302	total: 290ms	remaining: 1m 6s
13:	learn: 1.4633412	total: 312ms	remaining: 1m 6s
14:	learn: 1.4283317	total: 334ms	remaining: 1m 6s
15:	learn: 1.3945109	total: 357ms	remaining: 1m 6s
16:	learn: 1.3634220	total: 378ms	remaining: 1m 6s
17:	learn: 1.3343365	total: 399ms	remaining: 1m 6s
18:	learn: 1.3068944	tota

168:	learn: 0.7728388	total: 3.39s	remaining: 56.8s
169:	learn: 0.7725834	total: 3.42s	remaining: 56.9s
170:	learn: 0.7723799	total: 3.43s	remaining: 56.8s
171:	learn: 0.7719993	total: 3.45s	remaining: 56.8s
172:	learn: 0.7719417	total: 3.47s	remaining: 56.8s
173:	learn: 0.7718272	total: 3.49s	remaining: 56.7s
174:	learn: 0.7717265	total: 3.51s	remaining: 56.7s
175:	learn: 0.7715514	total: 3.53s	remaining: 56.6s
176:	learn: 0.7714948	total: 3.54s	remaining: 56.5s
177:	learn: 0.7714844	total: 3.56s	remaining: 56.5s
178:	learn: 0.7714401	total: 3.58s	remaining: 56.4s
179:	learn: 0.7713617	total: 3.6s	remaining: 56.4s
180:	learn: 0.7713452	total: 3.62s	remaining: 56.4s
181:	learn: 0.7711654	total: 3.64s	remaining: 56.3s
182:	learn: 0.7706789	total: 3.65s	remaining: 56.2s
183:	learn: 0.7703282	total: 3.67s	remaining: 56.2s
184:	learn: 0.7700919	total: 3.69s	remaining: 56.2s
185:	learn: 0.7697459	total: 3.71s	remaining: 56.1s
186:	learn: 0.7694434	total: 3.73s	remaining: 56.1s
187:	learn: 0

328:	learn: 0.7484212	total: 6.37s	remaining: 51.7s
329:	learn: 0.7482604	total: 6.39s	remaining: 51.7s
330:	learn: 0.7481278	total: 6.41s	remaining: 51.7s
331:	learn: 0.7481291	total: 6.43s	remaining: 51.6s
332:	learn: 0.7480378	total: 6.44s	remaining: 51.6s
333:	learn: 0.7480186	total: 6.46s	remaining: 51.6s
334:	learn: 0.7479277	total: 6.48s	remaining: 51.6s
335:	learn: 0.7477558	total: 6.5s	remaining: 51.5s
336:	learn: 0.7475660	total: 6.52s	remaining: 51.5s
337:	learn: 0.7474139	total: 6.54s	remaining: 51.5s
338:	learn: 0.7473359	total: 6.55s	remaining: 51.5s
339:	learn: 0.7471679	total: 6.58s	remaining: 51.5s
340:	learn: 0.7471074	total: 6.6s	remaining: 51.4s
341:	learn: 0.7470319	total: 6.61s	remaining: 51.4s
342:	learn: 0.7469158	total: 6.63s	remaining: 51.4s
343:	learn: 0.7469031	total: 6.65s	remaining: 51.4s
344:	learn: 0.7468120	total: 6.67s	remaining: 51.3s
345:	learn: 0.7467032	total: 6.69s	remaining: 51.3s
346:	learn: 0.7466989	total: 6.71s	remaining: 51.3s
347:	learn: 0.

490:	learn: 0.7341697	total: 9.5s	remaining: 48.6s
491:	learn: 0.7340686	total: 9.52s	remaining: 48.5s
492:	learn: 0.7339149	total: 9.54s	remaining: 48.5s
493:	learn: 0.7339070	total: 9.56s	remaining: 48.5s
494:	learn: 0.7338647	total: 9.57s	remaining: 48.5s
495:	learn: 0.7338205	total: 9.59s	remaining: 48.4s
496:	learn: 0.7338110	total: 9.61s	remaining: 48.4s
497:	learn: 0.7337255	total: 9.63s	remaining: 48.4s
498:	learn: 0.7337015	total: 9.64s	remaining: 48.3s
499:	learn: 0.7336606	total: 9.66s	remaining: 48.3s
500:	learn: 0.7335450	total: 9.68s	remaining: 48.3s
501:	learn: 0.7334714	total: 9.7s	remaining: 48.3s
502:	learn: 0.7334275	total: 9.72s	remaining: 48.3s
503:	learn: 0.7333911	total: 9.74s	remaining: 48.2s
504:	learn: 0.7333118	total: 9.76s	remaining: 48.2s
505:	learn: 0.7331761	total: 9.78s	remaining: 48.2s
506:	learn: 0.7331041	total: 9.8s	remaining: 48.2s
507:	learn: 0.7330709	total: 9.82s	remaining: 48.2s
508:	learn: 0.7330498	total: 9.84s	remaining: 48.1s
509:	learn: 0.7

659:	learn: 0.7256290	total: 12.6s	remaining: 44.8s
660:	learn: 0.7255061	total: 12.7s	remaining: 44.8s
661:	learn: 0.7254934	total: 12.7s	remaining: 44.8s
662:	learn: 0.7254624	total: 12.7s	remaining: 44.7s
663:	learn: 0.7254609	total: 12.7s	remaining: 44.7s
664:	learn: 0.7254195	total: 12.7s	remaining: 44.7s
665:	learn: 0.7253501	total: 12.8s	remaining: 44.7s
666:	learn: 0.7253111	total: 12.8s	remaining: 44.7s
667:	learn: 0.7252783	total: 12.8s	remaining: 44.7s
668:	learn: 0.7252700	total: 12.8s	remaining: 44.6s
669:	learn: 0.7252298	total: 12.8s	remaining: 44.6s
670:	learn: 0.7251733	total: 12.8s	remaining: 44.6s
671:	learn: 0.7250173	total: 12.9s	remaining: 44.6s
672:	learn: 0.7249366	total: 12.9s	remaining: 44.5s
673:	learn: 0.7248802	total: 12.9s	remaining: 44.5s
674:	learn: 0.7248339	total: 12.9s	remaining: 44.5s
675:	learn: 0.7247676	total: 12.9s	remaining: 44.5s
676:	learn: 0.7247510	total: 13s	remaining: 44.5s
677:	learn: 0.7246951	total: 13s	remaining: 44.4s
678:	learn: 0.72

...

2380:	learn: 0.6646424	total: 57.3s	remaining: 14.9s
2381:	learn: 0.6646168	total: 57.3s	remaining: 14.9s
2382:	learn: 0.6646022	total: 57.4s	remaining: 14.9s
2383:	learn: 0.6645847	total: 57.4s	remaining: 14.8s
2384:	learn: 0.6645670	total: 57.4s	remaining: 14.8s
2385:	learn: 0.6645610	total: 57.4s	remaining: 14.8s
2386:	learn: 0.6645468	total: 57.5s	remaining: 14.8s
2387:	learn: 0.6645283	total: 57.5s	remaining: 14.7s
2388:	learn: 0.6645087	total: 57.5s	remaining: 14.7s
2389:	learn: 0.6644939	total: 57.6s	remaining: 14.7s
2390:	learn: 0.6644752	total: 57.6s	remaining: 14.7s
2391:	learn: 0.6644556	total: 57.6s	remaining: 14.6s
2392:	learn: 0.6644398	total: 57.6s	remaining: 14.6s
2393:	learn: 0.6644168	total: 57.7s	remaining: 14.6s
2394:	learn: 0.6644077	total: 57.7s	remaining: 14.6s
2395:	learn: 0.6643979	total: 57.7s	remaining: 14.5s
2396:	learn: 0.6643971	total: 57.7s	remaining: 14.5s
2397:	learn: 0.6643985	total: 57.8s	remaining: 14.5s
2398:	learn: 0.6643897	total: 57.8s	remaining:

2546:	learn: 0.6618930	total: 1m 1s	remaining: 10.9s
2547:	learn: 0.6618732	total: 1m 1s	remaining: 10.9s
2548:	learn: 0.6618530	total: 1m 1s	remaining: 10.9s
2549:	learn: 0.6618333	total: 1m 1s	remaining: 10.8s
2550:	learn: 0.6618259	total: 1m 1s	remaining: 10.8s
2551:	learn: 0.6618056	total: 1m 1s	remaining: 10.8s
2552:	learn: 0.6617990	total: 1m 1s	remaining: 10.8s
2553:	learn: 0.6617840	total: 1m 1s	remaining: 10.7s
2554:	learn: 0.6617569	total: 1m 1s	remaining: 10.7s
2555:	learn: 0.6617511	total: 1m 1s	remaining: 10.7s
2556:	learn: 0.6617384	total: 1m 1s	remaining: 10.7s
2557:	learn: 0.6617076	total: 1m 1s	remaining: 10.6s
2558:	learn: 0.6616656	total: 1m 1s	remaining: 10.6s
2559:	learn: 0.6616508	total: 1m 1s	remaining: 10.6s
2560:	learn: 0.6616485	total: 1m 1s	remaining: 10.6s
2561:	learn: 0.6616368	total: 1m 1s	remaining: 10.5s
2562:	learn: 0.6616214	total: 1m 1s	remaining: 10.5s
2563:	learn: 0.6616013	total: 1m 1s	remaining: 10.5s
2564:	learn: 0.6615675	total: 1m 1s	remaining:

2707:	learn: 0.6593394	total: 1m 5s	remaining: 7.02s
2708:	learn: 0.6593149	total: 1m 5s	remaining: 6.99s
2709:	learn: 0.6593169	total: 1m 5s	remaining: 6.97s
2710:	learn: 0.6593059	total: 1m 5s	remaining: 6.95s
2711:	learn: 0.6592715	total: 1m 5s	remaining: 6.92s
2712:	learn: 0.6592628	total: 1m 5s	remaining: 6.9s
2713:	learn: 0.6592441	total: 1m 5s	remaining: 6.87s
2714:	learn: 0.6592109	total: 1m 5s	remaining: 6.85s
2715:	learn: 0.6591915	total: 1m 5s	remaining: 6.83s
2716:	learn: 0.6591762	total: 1m 5s	remaining: 6.8s
2717:	learn: 0.6591525	total: 1m 5s	remaining: 6.78s
2718:	learn: 0.6591262	total: 1m 5s	remaining: 6.75s
2719:	learn: 0.6590960	total: 1m 5s	remaining: 6.73s
2720:	learn: 0.6590909	total: 1m 5s	remaining: 6.71s
2721:	learn: 0.6590764	total: 1m 5s	remaining: 6.68s
2722:	learn: 0.6590663	total: 1m 5s	remaining: 6.66s
2723:	learn: 0.6590540	total: 1m 5s	remaining: 6.63s
2724:	learn: 0.6590254	total: 1m 5s	remaining: 6.61s
2725:	learn: 0.6589752	total: 1m 5s	remaining: 6

2868:	learn: 0.6568875	total: 1m 8s	remaining: 3.14s
2869:	learn: 0.6568756	total: 1m 8s	remaining: 3.12s
2870:	learn: 0.6568535	total: 1m 8s	remaining: 3.09s
2871:	learn: 0.6568318	total: 1m 8s	remaining: 3.07s
2872:	learn: 0.6568241	total: 1m 8s	remaining: 3.05s
2873:	learn: 0.6568140	total: 1m 8s	remaining: 3.02s
2874:	learn: 0.6568088	total: 1m 8s	remaining: 3s
2875:	learn: 0.6567702	total: 1m 8s	remaining: 2.97s
2876:	learn: 0.6566894	total: 1m 9s	remaining: 2.95s
2877:	learn: 0.6566773	total: 1m 9s	remaining: 2.93s
2878:	learn: 0.6566627	total: 1m 9s	remaining: 2.9s
2879:	learn: 0.6566357	total: 1m 9s	remaining: 2.88s
2880:	learn: 0.6566250	total: 1m 9s	remaining: 2.85s
2881:	learn: 0.6566129	total: 1m 9s	remaining: 2.83s
2882:	learn: 0.6566090	total: 1m 9s	remaining: 2.81s
2883:	learn: 0.6565931	total: 1m 9s	remaining: 2.78s
2884:	learn: 0.6565766	total: 1m 9s	remaining: 2.76s
2885:	learn: 0.6565670	total: 1m 9s	remaining: 2.73s
2886:	learn: 0.6565451	total: 1m 9s	remaining: 2.7

RandomizedSearchCV(cv=5,
                   estimator=<catboost.core.CatBoostRegressor object at 0x000001BD695CB850>,
                   param_distributions={'bootstrap_type': ['Bayesian',
                                                           'Bernoulli', 'MVS'],
                                        'eval_metric': ['MAE'],
                                        'iterations': range(1000, 4000, 1000),
                                        'l2_leaf_reg': range(1, 7),
                                        'learning_rate': [0.01, 0.05, 0.08, 0.1,
                                                          0.2],
                                        'random_seed': [42]},
                   scoring='neg_mean_absolute_error', verbose=3)

In [41]:
print(random_search.best_params_)
print(f"Точность модели по метрике MAE: {random_search.best_score_:0.2f}")

{'random_seed': 42, 'learning_rate': 0.1, 'l2_leaf_reg': 3, 'iterations': 3000, 'eval_metric': 'MAE', 'bootstrap_type': 'MVS'}
Точность модели по метрике MAE: -0.71


In [42]:
# Создадим тренировочную и валидационную выборки
x_tr_tr, x_tr_te, y_tr_tr, y_tr_te = train_test_split(x_train,
                                                      y_train,
                                                      test_size=0.2,
                                                      shuffle=True,
                                                      random_state=RANDOM_SEED) 

In [43]:
%%time
cbr_model = CatBoostRegressor(iterations = 3000,
                               learning_rate = 0.1,
                               l2_leaf_reg = 3,
                               random_seed = RANDOM_SEED,
                               eval_metric='MAE',
                               bootstrap_type = 'MVS')

cbr_model.fit(x_tr_tr, y_tr_tr,
               eval_set=(x_tr_te, y_tr_te),
               verbose_eval=100,
               use_best_model=True,
               plot=True)


MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 2.0766886	test: 2.0701584	best: 2.0701584 (0)	total: 32.8ms	remaining: 1m 38s
100:	learn: 0.7668521	test: 0.7650870	best: 0.7650870 (100)	total: 2.89s	remaining: 1m 22s
200:	learn: 0.7414916	test: 0.7438231	best: 0.7437621 (199)	total: 5.27s	remaining: 1m 13s
300:	learn: 0.7286499	test: 0.7340179	best: 0.7340179 (300)	total: 7.51s	remaining: 1m 7s
400:	learn: 0.7192139	test: 0.7272217	best: 0.7272217 (400)	total: 9.64s	remaining: 1m 2s
500:	learn: 0.7121081	test: 0.7227719	best: 0.7227548 (498)	total: 12.1s	remaining: 1m
600:	learn: 0.7068814	test: 0.7201951	best: 0.7201951 (600)	total: 14.4s	remaining: 57.5s
700:	learn: 0.7025054	test: 0.7181796	best: 0.7181594 (697)	total: 16.6s	remaining: 54.4s
800:	learn: 0.6991145	test: 0.7167335	best: 0.7167228 (796)	total: 18.5s	remaining: 50.9s
900:	learn: 0.6953124	test: 0.7152151	best: 0.7152151 (900)	total: 20.7s	remaining: 48.2s
1000:	learn: 0.6919711	test: 0.7140987	best: 0.7140983 (999)	total: 22.9s	remaining: 45.7s
1100:	learn:

In [44]:
cbr_predict = cbr_model.predict(x_val)
# оцениваем точность
print(f"Точность модели по метрике MAE: {(MAE(y_val, cbr_predict)):0.2f}")

Точность модели по метрике MAE: 0.71


In [45]:
%%time
estimate_cbr = -1 * cross_val_score(cbr_model,
                           x_train,
                           y_train,
                           cv=3,
                           scoring='neg_mean_absolute_error')

print(f"Точность модели по метрике MAE: {estimate_cbr.mean():0.2f}")

0:	learn: 2.0851997	total: 24.3ms	remaining: 1m 12s
1:	learn: 1.9460423	total: 44.8ms	remaining: 1m 7s
2:	learn: 1.8239507	total: 66.7ms	remaining: 1m 6s
3:	learn: 1.7136352	total: 86.1ms	remaining: 1m 4s
4:	learn: 1.6154146	total: 106ms	remaining: 1m 3s
5:	learn: 1.5265647	total: 127ms	remaining: 1m 3s
6:	learn: 1.4506396	total: 147ms	remaining: 1m 3s
7:	learn: 1.3840733	total: 167ms	remaining: 1m 2s
8:	learn: 1.3203852	total: 187ms	remaining: 1m 2s
9:	learn: 1.2668189	total: 209ms	remaining: 1m 2s
10:	learn: 1.2198758	total: 234ms	remaining: 1m 3s
11:	learn: 1.1769295	total: 254ms	remaining: 1m 3s
12:	learn: 1.1375360	total: 273ms	remaining: 1m 2s
13:	learn: 1.1033943	total: 293ms	remaining: 1m 2s
14:	learn: 1.0721640	total: 312ms	remaining: 1m 2s
15:	learn: 1.0441731	total: 332ms	remaining: 1m 1s
16:	learn: 1.0190758	total: 353ms	remaining: 1m 1s
17:	learn: 0.9963110	total: 374ms	remaining: 1m 1s
18:	learn: 0.9757437	total: 395ms	remaining: 1m 1s
19:	learn: 0.9581560	total: 418ms	re

171:	learn: 0.7445917	total: 3.12s	remaining: 51.3s
172:	learn: 0.7442502	total: 3.14s	remaining: 51.3s
173:	learn: 0.7440401	total: 3.16s	remaining: 51.3s
174:	learn: 0.7437790	total: 3.17s	remaining: 51.2s
175:	learn: 0.7432464	total: 3.19s	remaining: 51.2s
176:	learn: 0.7432763	total: 3.21s	remaining: 51.2s
177:	learn: 0.7431050	total: 3.23s	remaining: 51.2s
178:	learn: 0.7430621	total: 3.24s	remaining: 51.1s
179:	learn: 0.7429044	total: 3.26s	remaining: 51.1s
180:	learn: 0.7426162	total: 3.28s	remaining: 51.1s
181:	learn: 0.7422525	total: 3.29s	remaining: 51s
182:	learn: 0.7420300	total: 3.31s	remaining: 51s
183:	learn: 0.7418999	total: 3.33s	remaining: 51s
184:	learn: 0.7416732	total: 3.35s	remaining: 51s
185:	learn: 0.7414916	total: 3.36s	remaining: 50.9s
186:	learn: 0.7413448	total: 3.38s	remaining: 50.9s
187:	learn: 0.7413328	total: 3.4s	remaining: 50.9s
188:	learn: 0.7412487	total: 3.42s	remaining: 50.8s
189:	learn: 0.7412956	total: 3.43s	remaining: 50.8s
190:	learn: 0.7410187

337:	learn: 0.7216226	total: 5.97s	remaining: 47s
338:	learn: 0.7214743	total: 5.99s	remaining: 47s
339:	learn: 0.7213140	total: 6.01s	remaining: 47s
340:	learn: 0.7212840	total: 6.03s	remaining: 47s
341:	learn: 0.7211575	total: 6.05s	remaining: 47s
342:	learn: 0.7211173	total: 6.07s	remaining: 47s
343:	learn: 0.7210885	total: 6.08s	remaining: 47s
344:	learn: 0.7210035	total: 6.1s	remaining: 46.9s
345:	learn: 0.7208974	total: 6.12s	remaining: 46.9s
346:	learn: 0.7208044	total: 6.14s	remaining: 46.9s
347:	learn: 0.7206830	total: 6.16s	remaining: 46.9s
348:	learn: 0.7206209	total: 6.18s	remaining: 46.9s
349:	learn: 0.7206167	total: 6.19s	remaining: 46.9s
350:	learn: 0.7206089	total: 6.21s	remaining: 46.9s
351:	learn: 0.7204090	total: 6.23s	remaining: 46.9s
352:	learn: 0.7202431	total: 6.25s	remaining: 46.9s
353:	learn: 0.7201044	total: 6.27s	remaining: 46.9s
354:	learn: 0.7200801	total: 6.29s	remaining: 46.9s
355:	learn: 0.7200143	total: 6.31s	remaining: 46.8s
356:	learn: 0.7199469	total

501:	learn: 0.7100116	total: 8.82s	remaining: 43.9s
502:	learn: 0.7098736	total: 8.84s	remaining: 43.9s
503:	learn: 0.7098368	total: 8.86s	remaining: 43.9s
504:	learn: 0.7097809	total: 8.88s	remaining: 43.9s
505:	learn: 0.7097095	total: 8.9s	remaining: 43.9s
506:	learn: 0.7095972	total: 8.92s	remaining: 43.8s
507:	learn: 0.7094763	total: 8.93s	remaining: 43.8s
508:	learn: 0.7094021	total: 8.95s	remaining: 43.8s
509:	learn: 0.7093831	total: 8.97s	remaining: 43.8s
510:	learn: 0.7093758	total: 8.98s	remaining: 43.8s
511:	learn: 0.7092551	total: 9s	remaining: 43.7s
512:	learn: 0.7091369	total: 9.02s	remaining: 43.7s
513:	learn: 0.7091220	total: 9.04s	remaining: 43.7s
514:	learn: 0.7090426	total: 9.06s	remaining: 43.7s
515:	learn: 0.7090279	total: 9.08s	remaining: 43.7s
516:	learn: 0.7090185	total: 9.1s	remaining: 43.7s
517:	learn: 0.7089316	total: 9.12s	remaining: 43.7s
518:	learn: 0.7087638	total: 9.14s	remaining: 43.7s
519:	learn: 0.7086655	total: 9.16s	remaining: 43.7s
520:	learn: 0.708

661:	learn: 0.7014437	total: 11.6s	remaining: 41.1s
662:	learn: 0.7014342	total: 11.7s	remaining: 41.1s
663:	learn: 0.7013939	total: 11.7s	remaining: 41.1s
664:	learn: 0.7013048	total: 11.7s	remaining: 41.1s
665:	learn: 0.7013027	total: 11.7s	remaining: 41s
666:	learn: 0.7012519	total: 11.7s	remaining: 41s
667:	learn: 0.7012320	total: 11.7s	remaining: 41s
668:	learn: 0.7011951	total: 11.8s	remaining: 41s
669:	learn: 0.7011273	total: 11.8s	remaining: 41s
670:	learn: 0.7010773	total: 11.8s	remaining: 41s
671:	learn: 0.7010186	total: 11.8s	remaining: 41s
672:	learn: 0.7009993	total: 11.8s	remaining: 40.9s
673:	learn: 0.7009781	total: 11.9s	remaining: 40.9s
674:	learn: 0.7009145	total: 11.9s	remaining: 40.9s
675:	learn: 0.7008774	total: 11.9s	remaining: 40.9s
676:	learn: 0.7007681	total: 11.9s	remaining: 40.9s
677:	learn: 0.7007358	total: 11.9s	remaining: 40.8s
678:	learn: 0.7006836	total: 11.9s	remaining: 40.8s
679:	learn: 0.7005996	total: 12s	remaining: 40.8s
680:	learn: 0.7005705	total:

...

2246:	learn: 0.6541215	total: 42.5s	remaining: 14.2s
2247:	learn: 0.6541103	total: 42.5s	remaining: 14.2s
2248:	learn: 0.6540930	total: 42.5s	remaining: 14.2s
2249:	learn: 0.6540803	total: 42.5s	remaining: 14.2s
2250:	learn: 0.6540690	total: 42.5s	remaining: 14.2s
2251:	learn: 0.6540411	total: 42.6s	remaining: 14.1s
2252:	learn: 0.6539951	total: 42.6s	remaining: 14.1s
2253:	learn: 0.6539698	total: 42.6s	remaining: 14.1s
2254:	learn: 0.6539624	total: 42.6s	remaining: 14.1s
2255:	learn: 0.6539598	total: 42.6s	remaining: 14.1s
2256:	learn: 0.6539291	total: 42.6s	remaining: 14s
2257:	learn: 0.6539100	total: 42.7s	remaining: 14s
2258:	learn: 0.6539098	total: 42.7s	remaining: 14s
2259:	learn: 0.6539040	total: 42.7s	remaining: 14s
2260:	learn: 0.6538744	total: 42.7s	remaining: 14s
2261:	learn: 0.6538340	total: 42.7s	remaining: 13.9s
2262:	learn: 0.6538216	total: 42.8s	remaining: 13.9s
2263:	learn: 0.6538124	total: 42.8s	remaining: 13.9s
2264:	learn: 0.6538135	total: 42.8s	remaining: 13.9s
226

2411:	learn: 0.6506352	total: 45.5s	remaining: 11.1s
2412:	learn: 0.6506243	total: 45.5s	remaining: 11.1s
2413:	learn: 0.6506066	total: 45.5s	remaining: 11.1s
2414:	learn: 0.6505831	total: 45.5s	remaining: 11s
2415:	learn: 0.6505554	total: 45.6s	remaining: 11s
2416:	learn: 0.6505314	total: 45.6s	remaining: 11s
2417:	learn: 0.6505139	total: 45.6s	remaining: 11s
2418:	learn: 0.6504961	total: 45.6s	remaining: 11s
2419:	learn: 0.6504721	total: 45.6s	remaining: 10.9s
2420:	learn: 0.6504541	total: 45.7s	remaining: 10.9s
2421:	learn: 0.6504165	total: 45.7s	remaining: 10.9s
2422:	learn: 0.6503864	total: 45.7s	remaining: 10.9s
2423:	learn: 0.6503655	total: 45.7s	remaining: 10.9s
2424:	learn: 0.6503635	total: 45.7s	remaining: 10.8s
2425:	learn: 0.6503458	total: 45.7s	remaining: 10.8s
2426:	learn: 0.6503284	total: 45.8s	remaining: 10.8s
2427:	learn: 0.6502941	total: 45.8s	remaining: 10.8s
2428:	learn: 0.6502842	total: 45.8s	remaining: 10.8s
2429:	learn: 0.6502639	total: 45.8s	remaining: 10.7s
243

2570:	learn: 0.6472746	total: 48.3s	remaining: 8.06s
2571:	learn: 0.6472620	total: 48.3s	remaining: 8.04s
2572:	learn: 0.6472524	total: 48.4s	remaining: 8.03s
2573:	learn: 0.6472306	total: 48.4s	remaining: 8.01s
2574:	learn: 0.6472156	total: 48.4s	remaining: 7.99s
2575:	learn: 0.6472169	total: 48.4s	remaining: 7.97s
2576:	learn: 0.6471905	total: 48.4s	remaining: 7.95s
2577:	learn: 0.6471737	total: 48.5s	remaining: 7.93s
2578:	learn: 0.6471557	total: 48.5s	remaining: 7.91s
2579:	learn: 0.6471306	total: 48.5s	remaining: 7.89s
2580:	learn: 0.6471139	total: 48.5s	remaining: 7.88s
2581:	learn: 0.6470839	total: 48.5s	remaining: 7.86s
2582:	learn: 0.6470721	total: 48.5s	remaining: 7.84s
2583:	learn: 0.6470619	total: 48.6s	remaining: 7.82s
2584:	learn: 0.6470659	total: 48.6s	remaining: 7.8s
2585:	learn: 0.6470553	total: 48.6s	remaining: 7.78s
2586:	learn: 0.6470434	total: 48.6s	remaining: 7.76s
2587:	learn: 0.6470178	total: 48.6s	remaining: 7.74s
2588:	learn: 0.6470065	total: 48.6s	remaining: 

2733:	learn: 0.6440787	total: 51.2s	remaining: 4.98s
2734:	learn: 0.6440538	total: 51.2s	remaining: 4.96s
2735:	learn: 0.6440388	total: 51.2s	remaining: 4.94s
2736:	learn: 0.6440123	total: 51.2s	remaining: 4.92s
2737:	learn: 0.6440022	total: 51.2s	remaining: 4.9s
2738:	learn: 0.6439662	total: 51.3s	remaining: 4.88s
2739:	learn: 0.6439161	total: 51.3s	remaining: 4.87s
2740:	learn: 0.6439045	total: 51.3s	remaining: 4.85s
2741:	learn: 0.6438924	total: 51.3s	remaining: 4.83s
2742:	learn: 0.6438619	total: 51.3s	remaining: 4.81s
2743:	learn: 0.6438555	total: 51.3s	remaining: 4.79s
2744:	learn: 0.6438315	total: 51.4s	remaining: 4.77s
2745:	learn: 0.6438227	total: 51.4s	remaining: 4.75s
2746:	learn: 0.6438058	total: 51.4s	remaining: 4.73s
2747:	learn: 0.6437903	total: 51.4s	remaining: 4.71s
2748:	learn: 0.6437772	total: 51.4s	remaining: 4.7s
2749:	learn: 0.6437300	total: 51.4s	remaining: 4.68s
2750:	learn: 0.6437023	total: 51.5s	remaining: 4.66s
2751:	learn: 0.6437020	total: 51.5s	remaining: 4

2897:	learn: 0.6408808	total: 54.3s	remaining: 1.91s
2898:	learn: 0.6408604	total: 54.3s	remaining: 1.89s
2899:	learn: 0.6408612	total: 54.3s	remaining: 1.87s
2900:	learn: 0.6408499	total: 54.3s	remaining: 1.85s
2901:	learn: 0.6408253	total: 54.3s	remaining: 1.83s
2902:	learn: 0.6408106	total: 54.4s	remaining: 1.82s
2903:	learn: 0.6407844	total: 54.4s	remaining: 1.8s
2904:	learn: 0.6407670	total: 54.4s	remaining: 1.78s
2905:	learn: 0.6407433	total: 54.4s	remaining: 1.76s
2906:	learn: 0.6407284	total: 54.5s	remaining: 1.74s
2907:	learn: 0.6407100	total: 54.5s	remaining: 1.72s
2908:	learn: 0.6406824	total: 54.5s	remaining: 1.71s
2909:	learn: 0.6406690	total: 54.5s	remaining: 1.69s
2910:	learn: 0.6406396	total: 54.6s	remaining: 1.67s
2911:	learn: 0.6406212	total: 54.6s	remaining: 1.65s
2912:	learn: 0.6406058	total: 54.6s	remaining: 1.63s
2913:	learn: 0.6405810	total: 54.6s	remaining: 1.61s
2914:	learn: 0.6405690	total: 54.6s	remaining: 1.59s
2915:	learn: 0.6405559	total: 54.7s	remaining: 

### 4. GradientBoostingRegressor

In [46]:
%%time
gbr_model = GradientBoostingRegressor(random_state=RANDOM_SEED, n_estimators=200)
gbr_model.fit(x_train, y_train)

CPU times: total: 2min 5s
Wall time: 2min 5s


GradientBoostingRegressor(n_estimators=200, random_state=42)

In [47]:
gbr_predict = gbr_model.predict(x_val)

# оцениваем точность
print(f"Точность модели по метрике MAE: {(MAE(y_val, gbr_predict)):0.2f}")

Точность модели по метрике MAE: 0.77


In [48]:
%%time
estimate_gbr = -1 * cross_val_score(gbr_model,
                           x_train,
                           y_train,
                           cv=5,
                           scoring='neg_mean_absolute_error')

print(f"Точность модели по метрике MAE: {estimate_gbr.mean():0.2f}")

Точность модели по метрике MAE: 0.78
CPU times: total: 8min 5s
Wall time: 8min 6s


### 5. LightGBM

In [60]:
param_lgbmr_grid = {
    'n_estimators': [50, 100, 500, 700],
    'max_depth': range(3, 8, 1),
    'learning_rate': [0.01, 0.05, 0.08, 0.1, 0.2],
    'boosting_type': ['gbdt', 'dart', 'goss'],
    'random_seed': [RANDOM_SEED]
}

In [61]:
%%time
lgbm_reg = lgb.LGBMRegressor(objective='regression',
                             verbose=1)

random_search_lgbmr = RandomizedSearchCV(lgbm_reg,
                                   param_lgbmr_grid,
                                   cv=5,
                                   verbose = 3,
                                   scoring='neg_mean_absolute_error')
 
random_search_lgbmr.fit(x_train, y_train)

Fitting 5 folds for each of 10 candidates, totalling 50 fits
[CV 1/5] END boosting_type=goss, learning_rate=0.08, max_depth=3, n_estimators=700, random_seed=42;, score=-0.771 total time=   4.3s
[CV 2/5] END boosting_type=goss, learning_rate=0.08, max_depth=3, n_estimators=700, random_seed=42;, score=-1.037 total time=   4.6s
[CV 3/5] END boosting_type=goss, learning_rate=0.08, max_depth=3, n_estimators=700, random_seed=42;, score=-2017033016182.245 total time=   3.8s
[CV 4/5] END boosting_type=goss, learning_rate=0.08, max_depth=3, n_estimators=700, random_seed=42;, score=-0.767 total time=   3.8s
[CV 5/5] END boosting_type=goss, learning_rate=0.08, max_depth=3, n_estimators=700, random_seed=42;, score=-0.804 total time=   3.8s
[CV 1/5] END boosting_type=dart, learning_rate=0.1, max_depth=6, n_estimators=700, random_seed=42;, score=-0.722 total time=  48.8s
[CV 2/5] END boosting_type=dart, learning_rate=0.1, max_depth=6, n_estimators=700, random_seed=42;, score=-0.724 total time=  52.1

RandomizedSearchCV(cv=5,
                   estimator=LGBMRegressor(objective='regression', verbose=1),
                   param_distributions={'boosting_type': ['gbdt', 'dart',
                                                          'goss'],
                                        'learning_rate': [0.01, 0.05, 0.08, 0.1,
                                                          0.2],
                                        'max_depth': range(3, 8),
                                        'n_estimators': [50, 100, 500, 700],
                                        'random_seed': [42]},
                   scoring='neg_mean_absolute_error', verbose=3)

In [62]:
print(random_search_lgbmr.best_params_)
print(f"Точность модели по метрике MAE: {random_search_lgbmr.best_score_:0.2f}")

{'random_seed': 42, 'n_estimators': 700, 'max_depth': 6, 'learning_rate': 0.1, 'boosting_type': 'dart'}
Точность модели по метрике MAE: -0.72


In [64]:
lgbmr_model = lgb.LGBMRegressor(objective='regression',
                                max_depth=6,
                                learning_rate=0.1,
                                boosting_type='dart',
                                n_estimators=700,
                               random_seed=RANDOM_SEED)

lgbmr_model.fit(x_tr_tr, y_tr_tr,
                eval_set=(x_tr_te, y_tr_te),
                eval_metric='l1',
                early_stopping_rounds=5)

[1]	valid_0's l1: 2.06643	valid_0's l2: 6.6574
[2]	valid_0's l1: 1.92396	valid_0's l2: 5.69716
[3]	valid_0's l1: 1.7945	valid_0's l2: 4.91232
[4]	valid_0's l1: 1.67955	valid_0's l2: 4.27475
[5]	valid_0's l1: 1.57684	valid_0's l2: 3.75607
[6]	valid_0's l1: 1.48461	valid_0's l2: 3.33142
[7]	valid_0's l1: 1.50032	valid_0's l2: 3.39886
[8]	valid_0's l1: 1.41936	valid_0's l2: 3.04567
[9]	valid_0's l1: 1.34552	valid_0's l2: 2.75422
[10]	valid_0's l1: 1.37101	valid_0's l2: 2.85461
[11]	valid_0's l1: 1.30268	valid_0's l2: 2.59374
[12]	valid_0's l1: 1.32752	valid_0's l2: 2.68635
[13]	valid_0's l1: 1.2642	valid_0's l2: 2.45833
[14]	valid_0's l1: 1.20961	valid_0's l2: 2.27325
[15]	valid_0's l1: 1.15994	valid_0's l2: 2.12163
[16]	valid_0's l1: 1.11607	valid_0's l2: 1.9981
[17]	valid_0's l1: 1.13828	valid_0's l2: 2.05883
[18]	valid_0's l1: 1.09705	valid_0's l2: 1.9449
[19]	valid_0's l1: 1.10184	valid_0's l2: 1.95807
[20]	valid_0's l1: 1.10578	valid_0's l2: 1.96869
[21]	valid_0's l1: 1.13759	valid_0

[167]	valid_0's l1: 0.966341	valid_0's l2: 1.79407
[168]	valid_0's l1: 0.931506	valid_0's l2: 1.7141
[169]	valid_0's l1: 0.90124	valid_0's l2: 1.64805
[170]	valid_0's l1: 0.913363	valid_0's l2: 1.67725
[171]	valid_0's l1: 0.928957	valid_0's l2: 1.71289
[172]	valid_0's l1: 0.898874	valid_0's l2: 1.64738
[173]	valid_0's l1: 0.873598	valid_0's l2: 1.59464
[174]	valid_0's l1: 0.886107	valid_0's l2: 1.62179
[175]	valid_0's l1: 0.862301	valid_0's l2: 1.57327
[176]	valid_0's l1: 0.842192	valid_0's l2: 1.53319
[177]	valid_0's l1: 0.853615	valid_0's l2: 1.55872
[178]	valid_0's l1: 0.834489	valid_0's l2: 1.52162
[179]	valid_0's l1: 0.818757	valid_0's l2: 1.49167
[180]	valid_0's l1: 0.82948	valid_0's l2: 1.51425
[181]	valid_0's l1: 0.844215	valid_0's l2: 1.5435
[182]	valid_0's l1: 0.919915	valid_0's l2: 1.67035
[183]	valid_0's l1: 0.891294	valid_0's l2: 1.61188
[184]	valid_0's l1: 0.904226	valid_0's l2: 1.64049
[185]	valid_0's l1: 0.878245	valid_0's l2: 1.58889
[186]	valid_0's l1: 0.890868	valid_

[328]	valid_0's l1: 0.753108	valid_0's l2: 1.36419
[329]	valid_0's l1: 0.757808	valid_0's l2: 1.37075
[330]	valid_0's l1: 0.762044	valid_0's l2: 1.37711
[331]	valid_0's l1: 0.765727	valid_0's l2: 1.38299
[332]	valid_0's l1: 0.759092	valid_0's l2: 1.37302
[333]	valid_0's l1: 0.763235	valid_0's l2: 1.37946
[334]	valid_0's l1: 0.772032	valid_0's l2: 1.4017
[335]	valid_0's l1: 0.764074	valid_0's l2: 1.38847
[336]	valid_0's l1: 0.769526	valid_0's l2: 1.39704
[337]	valid_0's l1: 0.774482	valid_0's l2: 1.40537
[338]	valid_0's l1: 0.7662	valid_0's l2: 1.39169
[339]	valid_0's l1: 0.771585	valid_0's l2: 1.39968
[340]	valid_0's l1: 0.76356	valid_0's l2: 1.38662
[341]	valid_0's l1: 0.76815	valid_0's l2: 1.394
[342]	valid_0's l1: 0.760765	valid_0's l2: 1.38196
[343]	valid_0's l1: 0.765653	valid_0's l2: 1.38958
[344]	valid_0's l1: 0.758498	valid_0's l2: 1.37813
[345]	valid_0's l1: 0.752556	valid_0's l2: 1.36883
[346]	valid_0's l1: 0.757325	valid_0's l2: 1.3758
[347]	valid_0's l1: 0.751705	valid_0's 

[491]	valid_0's l1: 0.726121	valid_0's l2: 1.32339
[492]	valid_0's l1: 0.724824	valid_0's l2: 1.32157
[493]	valid_0's l1: 0.725985	valid_0's l2: 1.32418
[494]	valid_0's l1: 0.727361	valid_0's l2: 1.32718
[495]	valid_0's l1: 0.735258	valid_0's l2: 1.33484
[496]	valid_0's l1: 0.737658	valid_0's l2: 1.33868
[497]	valid_0's l1: 0.734481	valid_0's l2: 1.334
[498]	valid_0's l1: 0.731676	valid_0's l2: 1.32995
[499]	valid_0's l1: 0.733698	valid_0's l2: 1.33316
[500]	valid_0's l1: 0.736011	valid_0's l2: 1.33691
[501]	valid_0's l1: 0.732714	valid_0's l2: 1.33241
[502]	valid_0's l1: 0.735024	valid_0's l2: 1.33619
[503]	valid_0's l1: 0.731826	valid_0's l2: 1.33175
[504]	valid_0's l1: 0.733887	valid_0's l2: 1.3353
[505]	valid_0's l1: 0.736171	valid_0's l2: 1.33893
[506]	valid_0's l1: 0.732822	valid_0's l2: 1.33403
[507]	valid_0's l1: 0.730304	valid_0's l2: 1.33029
[508]	valid_0's l1: 0.727917	valid_0's l2: 1.32683
[509]	valid_0's l1: 0.72594	valid_0's l2: 1.32363
[510]	valid_0's l1: 0.727685	valid_

[653]	valid_0's l1: 0.720603	valid_0's l2: 1.31323
[654]	valid_0's l1: 0.718786	valid_0's l2: 1.31093
[655]	valid_0's l1: 0.719894	valid_0's l2: 1.31284
[656]	valid_0's l1: 0.718193	valid_0's l2: 1.3104
[657]	valid_0's l1: 0.716787	valid_0's l2: 1.30852
[658]	valid_0's l1: 0.715518	valid_0's l2: 1.3069
[659]	valid_0's l1: 0.714591	valid_0's l2: 1.30565
[660]	valid_0's l1: 0.715461	valid_0's l2: 1.30729
[661]	valid_0's l1: 0.714273	valid_0's l2: 1.30558
[662]	valid_0's l1: 0.713533	valid_0's l2: 1.30452
[663]	valid_0's l1: 0.714372	valid_0's l2: 1.30599
[664]	valid_0's l1: 0.715099	valid_0's l2: 1.30744
[665]	valid_0's l1: 0.716167	valid_0's l2: 1.3091
[666]	valid_0's l1: 0.714967	valid_0's l2: 1.3074
[667]	valid_0's l1: 0.715954	valid_0's l2: 1.30919
[668]	valid_0's l1: 0.714812	valid_0's l2: 1.30729
[669]	valid_0's l1: 0.716028	valid_0's l2: 1.30913
[670]	valid_0's l1: 0.714854	valid_0's l2: 1.30716
[671]	valid_0's l1: 0.71385	valid_0's l2: 1.30577
[672]	valid_0's l1: 0.715208	valid_0

LGBMRegressor(boosting_type='dart', max_depth=6, n_estimators=700,
              objective='regression', random_seed=42)

In [65]:
# Прогноз тестовой машины
lgbmr_pred = lgbmr_model.predict(x_val, num_iteration=lgbmr_model.best_iteration_)
# Оценка модели
print(f"Точность модели по метрике MAE: {(MAE(y_val, lgbmr_pred)):0.2f}")

Точность модели по метрике MAE: 0.71


In [66]:
%%time
estimate_lgbmr = -1 * cross_val_score(lgbmr_model,
                           x_train,
                           y_train,
                           cv=3,
                           scoring='neg_mean_absolute_error')

print(f"Точность модели по метрике MAE: {estimate_lgbmr.mean():0.2f}")

Точность модели по метрике MAE: 0.72
CPU times: total: 14min 55s
Wall time: 2min 5s


### 6. Blanding with RandomForestRegressor and CatBoostRegressor

In [57]:
%%time
bl_models = [cbr_model, rfr_model]

def blanding_model_predict(d_models, d_X_train, d_y_train, d_X_val):
    d_df = pd.DataFrame()
    for model_ in tqdm(d_models):
        model_.fit(d_X_train, d_y_train)
        y_pred = model_.predict(d_X_val)
        d_df[str(model_)[:6]] = y_pred               
    return d_df

temp_df = blanding_model_predict(bl_models, x_train, y_train, x_val)
temp_df['y_pred'] = temp_df.mean(axis=1)

  0%|          | 0/2 [00:00<?, ?it/s]

0:	learn: 2.0756966	total: 36.6ms	remaining: 1m 49s
1:	learn: 1.9407396	total: 60.8ms	remaining: 1m 31s
2:	learn: 1.8181942	total: 85ms	remaining: 1m 24s
3:	learn: 1.7082658	total: 111ms	remaining: 1m 23s
4:	learn: 1.6079430	total: 140ms	remaining: 1m 24s
5:	learn: 1.5210725	total: 166ms	remaining: 1m 22s
6:	learn: 1.4443351	total: 192ms	remaining: 1m 21s
7:	learn: 1.3776064	total: 218ms	remaining: 1m 21s
8:	learn: 1.3159104	total: 246ms	remaining: 1m 21s
9:	learn: 1.2622451	total: 270ms	remaining: 1m 20s
10:	learn: 1.2145027	total: 293ms	remaining: 1m 19s
11:	learn: 1.1716367	total: 319ms	remaining: 1m 19s
12:	learn: 1.1335776	total: 344ms	remaining: 1m 19s
13:	learn: 1.0992552	total: 370ms	remaining: 1m 18s
14:	learn: 1.0688753	total: 391ms	remaining: 1m 17s
15:	learn: 1.0417044	total: 414ms	remaining: 1m 17s
16:	learn: 1.0171157	total: 442ms	remaining: 1m 17s
17:	learn: 0.9955100	total: 469ms	remaining: 1m 17s
18:	learn: 0.9760967	total: 490ms	remaining: 1m 16s
19:	learn: 0.9577309	

163:	learn: 0.7478232	total: 4.11s	remaining: 1m 11s
164:	learn: 0.7475593	total: 4.14s	remaining: 1m 11s
165:	learn: 0.7471583	total: 4.17s	remaining: 1m 11s
166:	learn: 0.7467265	total: 4.19s	remaining: 1m 11s
167:	learn: 0.7467430	total: 4.21s	remaining: 1m 11s
168:	learn: 0.7464845	total: 4.24s	remaining: 1m 10s
169:	learn: 0.7462780	total: 4.26s	remaining: 1m 10s
170:	learn: 0.7461145	total: 4.28s	remaining: 1m 10s
171:	learn: 0.7461126	total: 4.31s	remaining: 1m 10s
172:	learn: 0.7458193	total: 4.34s	remaining: 1m 10s
173:	learn: 0.7455764	total: 4.36s	remaining: 1m 10s
174:	learn: 0.7454488	total: 4.38s	remaining: 1m 10s
175:	learn: 0.7451702	total: 4.41s	remaining: 1m 10s
176:	learn: 0.7449666	total: 4.43s	remaining: 1m 10s
177:	learn: 0.7447820	total: 4.45s	remaining: 1m 10s
178:	learn: 0.7444837	total: 4.48s	remaining: 1m 10s
179:	learn: 0.7441885	total: 4.5s	remaining: 1m 10s
180:	learn: 0.7439826	total: 4.53s	remaining: 1m 10s
181:	learn: 0.7436395	total: 4.59s	remaining: 1

320:	learn: 0.7243950	total: 8.13s	remaining: 1m 7s
321:	learn: 0.7243261	total: 8.15s	remaining: 1m 7s
322:	learn: 0.7242685	total: 8.18s	remaining: 1m 7s
323:	learn: 0.7242683	total: 8.21s	remaining: 1m 7s
324:	learn: 0.7242648	total: 8.23s	remaining: 1m 7s
325:	learn: 0.7240918	total: 8.26s	remaining: 1m 7s
326:	learn: 0.7239878	total: 8.28s	remaining: 1m 7s
327:	learn: 0.7239794	total: 8.31s	remaining: 1m 7s
328:	learn: 0.7238701	total: 8.33s	remaining: 1m 7s
329:	learn: 0.7237193	total: 8.36s	remaining: 1m 7s
330:	learn: 0.7236854	total: 8.39s	remaining: 1m 7s
331:	learn: 0.7236827	total: 8.41s	remaining: 1m 7s
332:	learn: 0.7236098	total: 8.44s	remaining: 1m 7s
333:	learn: 0.7235664	total: 8.46s	remaining: 1m 7s
334:	learn: 0.7234632	total: 8.49s	remaining: 1m 7s
335:	learn: 0.7233112	total: 8.51s	remaining: 1m 7s
336:	learn: 0.7232914	total: 8.54s	remaining: 1m 7s
337:	learn: 0.7231400	total: 8.56s	remaining: 1m 7s
338:	learn: 0.7230170	total: 8.58s	remaining: 1m 7s
339:	learn: 

483:	learn: 0.7138345	total: 12.2s	remaining: 1m 3s
484:	learn: 0.7138187	total: 12.2s	remaining: 1m 3s
485:	learn: 0.7137256	total: 12.3s	remaining: 1m 3s
486:	learn: 0.7136603	total: 12.3s	remaining: 1m 3s
487:	learn: 0.7136527	total: 12.3s	remaining: 1m 3s
488:	learn: 0.7135592	total: 12.4s	remaining: 1m 3s
489:	learn: 0.7135570	total: 12.4s	remaining: 1m 3s
490:	learn: 0.7135048	total: 12.4s	remaining: 1m 3s
491:	learn: 0.7133975	total: 12.4s	remaining: 1m 3s
492:	learn: 0.7133258	total: 12.5s	remaining: 1m 3s
493:	learn: 0.7132543	total: 12.5s	remaining: 1m 3s
494:	learn: 0.7132538	total: 12.5s	remaining: 1m 3s
495:	learn: 0.7131872	total: 12.5s	remaining: 1m 3s
496:	learn: 0.7130979	total: 12.6s	remaining: 1m 3s
497:	learn: 0.7130399	total: 12.6s	remaining: 1m 3s
498:	learn: 0.7130375	total: 12.6s	remaining: 1m 3s
499:	learn: 0.7129149	total: 12.6s	remaining: 1m 3s
500:	learn: 0.7128607	total: 12.7s	remaining: 1m 3s
501:	learn: 0.7127872	total: 12.7s	remaining: 1m 3s
502:	learn: 

...

building tree 121 of 500
building tree 122 of 500
building tree 123 of 500
building tree 124 of 500
building tree 125 of 500
building tree 126 of 500
building tree 127 of 500
building tree 128 of 500
building tree 129 of 500
building tree 130 of 500
building tree 131 of 500
building tree 132 of 500
building tree 133 of 500
building tree 134 of 500
building tree 135 of 500
building tree 136 of 500
building tree 137 of 500
building tree 138 of 500
building tree 139 of 500
building tree 140 of 500
building tree 141 of 500
building tree 142 of 500
building tree 143 of 500
building tree 144 of 500
building tree 145 of 500
building tree 146 of 500
building tree 147 of 500
building tree 148 of 500
building tree 149 of 500
building tree 150 of 500
building tree 151 of 500
building tree 152 of 500
building tree 153 of 500
building tree 154 of 500
building tree 155 of 500
building tree 156 of 500
building tree 157 of 500
building tree 158 of 500
building tree 159 of 500
building tree 160 of 500


[Parallel(n_jobs=-1)]: Done 272 tasks      | elapsed:  2.3min


building tree 281 of 500
building tree 282 of 500
building tree 283 of 500
building tree 284 of 500
building tree 285 of 500
building tree 286 of 500
building tree 287 of 500
building tree 288 of 500
building tree 289 of 500
building tree 290 of 500
building tree 291 of 500
building tree 292 of 500
building tree 293 of 500
building tree 294 of 500
building tree 295 of 500
building tree 296 of 500
building tree 297 of 500
building tree 298 of 500
building tree 299 of 500
building tree 300 of 500
building tree 301 of 500
building tree 302 of 500
building tree 303 of 500
building tree 304 of 500
building tree 305 of 500
building tree 306 of 500
building tree 307 of 500
building tree 308 of 500
building tree 309 of 500
building tree 310 of 500
building tree 311 of 500
building tree 312 of 500
building tree 313 of 500
building tree 314 of 500
building tree 315 of 500
building tree 316 of 500
building tree 317 of 500
building tree 318 of 500
building tree 319 of 500
building tree 320 of 500


[Parallel(n_jobs=-1)]: Done 500 out of 500 | elapsed:  4.2min finished
[Parallel(n_jobs=8)]: Using backend ThreadingBackend with 8 concurrent workers.
[Parallel(n_jobs=8)]: Done  16 tasks      | elapsed:    0.0s
[Parallel(n_jobs=8)]: Done 112 tasks      | elapsed:    0.3s
[Parallel(n_jobs=8)]: Done 272 tasks      | elapsed:    0.8s
[Parallel(n_jobs=8)]: Done 500 out of 500 | elapsed:    1.4s finished
100%|██████████| 2/2 [05:40<00:00, 170.46s/it]

CPU times: total: 38min 31s
Wall time: 5min 41s


In [58]:
bl_predict = np.array(temp_df['y_pred'])

# оцениваем точность
print(f"Точность модели по метрике MAE: {(MAE(y_val, bl_predict)):0.2f}")

Точность модели по метрике MAE: 0.69
